In [3]:
# utility packages
import os
import numpy as np
from load_data import get_dataset, encode_data
from models import Contrastive_model, FineTuneModel
from trainer import train_model, train_finetune_model

#plotting
import plotly.express as px
import plotly.io as pio
from umap import UMAP

# sklearn
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, confusion_matrix, ConfusionMatrixDisplay

# pytorch
import torch
from torch.utils.data import TensorDataset, DataLoader

# Mode
train = False
test = "contrastive"  # contrastive, finetune, from_scratch
experiment = 1

# Constants
width_original = 1024
height_original = 570
undersample = "random"
seq_length = 30
classes = 4
batch_size = 64
original_features = 56  # 28x2
extracted_features = 64
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#pio.renderers.default = 'browser'

behavior_class = {0: "attack",
                  1: "investigation",
                  2: "mount",
                  3: "other"}


X_train_encoded = np.load(os.path.join(os.getcwd(), "Embeddings", "X_train_encoded.npy"))
X_valid_hc = np.load(os.path.join(os.getcwd(), "Embeddings", "X_valid_hc.npy"))
X_valid = np.load(os.path.join(os.getcwd(), "Embeddings", "X_valid.npy"))
y_valid = np.load(os.path.join(os.getcwd(), "Embeddings", "y_valid.npy"))
train_size = len(X_valid)

In [5]:
# visualize embeddings using UMAP
umap_2d = UMAP(n_components=2, init='random', random_state=42)
viz_results1 = umap_2d.fit_transform(np.squeeze(X_valid).reshape(train_size, -1))

# visualize embeddings using UMAP
umap_2d = UMAP(n_components=2, init='random', random_state=42)
viz_results2 = umap_2d.fit_transform(np.squeeze(X_valid_hc).reshape(train_size, -1))

# visualize embeddings using UMAP
umap_2d = UMAP(n_components=2, init='random', random_state=42)
viz_results3 = umap_2d.fit_transform(X_train_encoded)

In [6]:
#cmap = px.colors.qualitative.Plotly
cmap = ['#636EFA', '#EF553B', 'rgb(246, 207, 113)', '#19D3F3']

In [7]:
# plot original embeddings
fig = px.scatter(viz_results1, x=0, y=1, color=np.vectorize(behavior_class.__getitem__)(y_valid.astype(int)),
                 labels={'0': 'UMAP 1', '1': 'UMAP 2'}, title="Original Feature Representation",
                 color_discrete_sequence=cmap)
fig.update_layout(legend_title_text='Behavior')
fig.show()

# plot handcrafted embeddings
fig = px.scatter(viz_results2, x=0, y=1, color=np.vectorize(behavior_class.__getitem__)(y_valid.astype(int)),
                 labels={'0': 'UMAP 1', '1': 'UMAP 2'}, title="Handcrafted Feature Representation",
                 color_discrete_sequence=cmap)
fig.update_layout(legend_title_text='Behavior')
fig.show()

# plot learnt embeddings
fig = px.scatter(viz_results3, x=0, y=1, color=np.vectorize(behavior_class.__getitem__)(y_valid.astype(int)),
                 labels={'0': 'UMAP 1', '1': 'UMAP 2'}, title="Learnt Feature Representation",
                 color_discrete_sequence=cmap)
fig.update_layout(legend_title_text='Behavior')
fig.show()

In [ ]:
print(px.colors.qualitative.Plotly)